In [1]:
import plotly.io as pio
pio.renderers.default = "png"  # save static images in outputs (needs kaleido)


# # **Python Project:Stock Data Analysis with pandas and plotly**
**Author**:Pradumn Chauhan



## **Project Overview**  
This project analyzes the historical performance of the following stocks over **6 years (Aug 2019–Aug 2025)**:  
1. **Chambal Fertilisers & Chemicals Ltd** (CHAMBLFERT)  
2. **PG Electroplast Ltd** (PGEL)  
3. **KEC International Ltd** (KEC)  
4. **HUDCO** (Housing & Urban Development Corp)  
5. **Titagarh**  (Titagarh Railsystems)

**Key Metrics Calculated:**  
- Daily/Weekly Price Volatility (Standard Deviation, Beta)  
- Cumulative Returns  
- Daily Percentage Change  
- Moving Averages (50-day, 200-day)  
- Correlation Heatmap (Inter-stock relationships)


## **Tools & Libraries Used**  
- **Python** (Pandas, NumPy, Matplotlib, Seaborn)  
- **Data Sources:** Yahoo Finance, CSV/Excel exports  
- **Visualization:** Plotly, Candlestick Charts, Line Plots 

In [2]:
# Data and array manipulation
import pandas as pd
import numpy as np

# Datetime manipulation
# import datetime as dt
import yfinance as yf
import pandas as pd
from datetime import datetime, timedelta

# Plotting and Visualization
import matplotlib.pyplot as plt
import plotly.express as px
import chart_studio.plotly as py
import cufflinks as cf


# Interactive charts
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected = True)
cf.go_offline()

# Options
pd.options.display.float_format = '{:,.4f}'.format

# Default settings
default_yaxis = dict(showgrid = False,
                     zeroline = False,
                     showline = False,
                     showticklabels = True)
default_RgSlct = dict(buttons = list([dict(count = 1, label = "1 Month", step = "month", stepmode = "backward"),
                                      dict(count = 6, label = "6 Months", step = "month", stepmode = "backward"),
                                      dict(count = 1, label = "1 Year", step = "year", stepmode = "backward"),
                                      dict(count = 1, label = "YTD", step = "year", stepmode = "todate"),
                                      dict(label = "All Data", step = "all")]))

**Reading Data**
In this project i will consider the data of last 6 years(2019-2025).This data is downloaded using pyfinance library(by yahoo)

In [3]:


# Define tickers
tickers = ['PGEL.NS', 'TITAGARH.NS', 'CHAMBLFERT.NS', 'HUDCO.NS', 'KEC.NS']

# Calculate date range (6 years back from today)
end_date = datetime.today()
start_date = end_date - timedelta(days=6*365)

# Download data
data = yf.download(tickers, start=start_date, end=end_date)

# Reshape and format the data
df_list = []
for ticker in tickers:
    temp = data.xs(ticker, level=1, axis=1).reset_index()
    temp['Ticker'] = ticker
    temp = temp.rename(columns={'Date': 'Date', 'High': 'High', 'Low': 'Low', 
                               'Open': 'Open', 'Close': 'Close', 
                               'Volume': 'Volume', 'Adj Close': 'Adj Close'})
    df_list.append(temp)

final_df = pd.concat(df_list)
final_df = final_df.sort_values(['Ticker', 'Date']).reset_index(drop=True)

# Save to CSV
final_df.to_csv('indian_stocks_6years.csv')

C:\Users\Pradumn Chauhan\AppData\Local\Temp\ipykernel_21472\3898462888.py:9: FutureWarning:

YF.download() has changed argument auto_adjust default to True

[*********************100%***********************]  5 of 5 completed


In [4]:
final_df.head()  

Price       Date    Close     High      Low     Open  Volume         Ticker
0     2019-08-22 115.6232 119.1992 113.9204 119.1992  148008  CHAMBLFERT.NS
1     2019-08-23 126.9471 128.9905 115.5806 117.2409  256655  CHAMBLFERT.NS
2     2019-08-26 127.2451 128.5648 124.1800 127.7134  126644  CHAMBLFERT.NS
3     2019-08-27 126.0532 129.8420 124.3929 127.7134  279683  CHAMBLFERT.NS
4     2019-08-28 129.8845 131.7577 126.0106 126.0106  485555  CHAMBLFERT.NS

In [5]:
#this gives count of null values in each column
final_df.isnull().sum() 

Price
Date      0
Close     0
High      0
Low       0
Open      0
Volume    0
Ticker    0
dtype: int64

In [6]:
final_df.groupby('Ticker')['Date'].agg(['min','max','count'])

min        max  count
Ticker                                    
CHAMBLFERT.NS 2019-08-22 2025-08-20   1484
HUDCO.NS      2019-08-22 2025-08-20   1484
KEC.NS        2019-08-22 2025-08-20   1484
PGEL.NS       2019-08-22 2025-08-20   1484
TITAGARH.NS   2019-08-22 2025-08-20   1484

**Trend Analysis**

Firstly, let us look at the line charts of all the stocks separately, this only gives a rough image of the trends in the changes in these stock prices over the chosen period, but it is a good start to study these trends. I prefer area charts to line charts as their visual effect is stronger for my eyes to realize the magnitude of each stock price compared to those of others.

In [7]:
fig=px.area(final_df,
        x='Date',
        y='Open',
        facet_col='Ticker',
        facet_col_wrap=2,
        labels={'x':'date','y':'price'},
        title='Opening Price of Chosen stocks',
        width=1200,
        height=700)

fig.update_layout(yaxis=default_yaxis,showlegend=False,autosize=True, plot_bgcolor='white')

#showing the visualization

fig.show()

In [8]:
#creating the basic line chart

fig_2=px.line(final_df,
        x='Date',
        y='Open',
        color='Ticker',
        labels={'x':'Date', 'y':'price'},
        title='Opening Price Of Chosen Stocks',
        width=1200,
        height=700)

#updating the layout of the chart

fig_2.update_layout(yaxis=default_yaxis,autosize=True,plot_bgcolor='white')

#creating the slider
fig_2.update_xaxes(rangeselector=default_RgSlct)

fig_2.show()

The line plot illustrates not only the differences in price among the stocks, but it also shows similarities in the changes of these prices. A dramatically decreasing trend can be observed in the prices of all stocks from the end of February to March 19, 2020 and second decreasing trend recently because of Tariff(imposed by US).

This shows that the fears of Coronavirus affected the whole market and Tariffs can change sentiments for short time too.

These plots illustrate only differences in prices, but they are not sufficient to learn everything about these stocks. The price of company's stock reflects how the market evaluates that stock, but it does not necessarily reflect the value of the company. Hence, more investigation into the traded volume is necessary.


In [9]:
fig_3=px.line(final_df,
        x='Date',
        y='Volume',
        color='Ticker',
        labels={'x':'Date','y':'Volume'},
        title='Traded Volume of Chosen Stocks',
        width=1000,
        height=600
    )

#Updating the layout of the chart
fig_3.update_layout(yaxis=default_yaxis,autosize=True, plot_bgcolor='white')

#creating the slider
fig_3.update_xaxes(rangeselector=default_RgSlct)

fig_3.show()




The plot of traded volume shows a totally opposite image to that of the price plot. It can be seen that **HUDCO.NS** and **CHAMBLFERT.NS** have high traded volume compared to those of others over the considered period. It seems to be the case that stocks whose prices are low have high traded volume, so it would be better if the daily total traded value is investigated, but this data is not available.

Fortunately, a proxy for this data can be constructed and used to get more insight about it. Since we have data about High and Low prices of a stock as well as the traded Volume of the trading days, a proxy for the daily traded value can be calculated using the following formula

$$
                                                                   Traded Value~1/2*(High+Low)*Volume
$$


In [10]:
final_df['Traded value']=0.5*(final_df['High']+final_df['Low'])*final_df['Volume']

#creating the line chart for traded value
fig_4=px.line(final_df,
            x='Date',
            y='Traded value',
            color='Ticker',
            title='Traded Value of Chosen Stocks',
            width=1000,
            height=600)

#Updating the layout of the chart
fig_4.update_layout(yaxis=default_yaxis,autosize=True,plot_bgcolor='white')

#creating the slider
fig_4.update_xaxes(rangeselector=default_RgSlct)

fig_4.show()


The illustration now shows a clearer view of the changes among the stocks. Visually speaking, the changes in traded value of **KEC.NS** and **TITAGARH.NS** seem to have many spikes over the considered period. This phenomenon might be caused either by the sudden changes in one the stock price or in traded volume. Let us have a deeper look at the summarized statistics of these stocks

In [11]:
r_show=[('Open', 'count'),
        ('Open','mean'),
        ('Open','std'),
        ('Open','mean/std'),
        ('Volume','mean'),
        ('Volume','std'),
        ('Volume','mean/std'),
        ('Traded value','mean'),
        ('Traded value','std'),
        ('Traded value','mean/std')]


#Create summary table of chosen variable
tab_sum1=final_df.loc[:,['Ticker','Open','Volume','Traded value']].groupby('Ticker').describe()

#Calculating of mean/std

tab_sum1[('Open','mean/std')]=tab_sum1[('Open','mean')]/tab_sum1[('Open','std')]
tab_sum1[('Volume','mean/std')]=tab_sum1[('Volume','mean')]/tab_sum1[('Volume','std')]
tab_sum1[('Traded value','mean/std')]=tab_sum1[('Traded value','mean')]/tab_sum1[('Traded value','std')]


#showing sorted result
tab_sum1=tab_sum1.loc[:,r_show]

#sorting the values

tab_sum1.sort_values(by=[('Traded value','mean')],ascending=False)


Price               Open                                    Volume  \
                   count     mean      std mean/std           mean   
Ticker                                                               
HUDCO.NS      1,484.0000  87.7539  85.7161   1.0238 7,804,760.3100   
TITAGARH.NS   1,484.0000 428.7317 471.0347   0.9102 1,264,981.8221   
CHAMBLFERT.NS 1,484.0000 310.6679 138.5092   2.2429 1,946,354.0836   
KEC.NS        1,484.0000 522.8843 229.7435   2.2759   664,320.0047   
PGEL.NS       1,484.0000 205.6751 270.2820   0.7610   990,729.0438   

Price                                        Traded value                     \
                          std mean/std               mean                std   
Ticker                                                                         
HUDCO.NS      15,118,781.5638   0.5162 1,089,881,671.4356 2,601,100,930.1765   
TITAGARH.NS    1,626,437.6470   0.7778   781,703,469.0596 1,676,104,373.9618   
CHAMBLFERT.NS  2,508,507.8053   0.7759   705,051,873.7898 1,188,377,129.4900   
KEC.NS         1,348,234.5054   0.4927   417,241,590.9233 1,099,147,840.9824   
PGEL.NS        2,029,635.0606   0.4881   346,438,019.2746 1,107,625,517.1846   

Price                   
              mean/std  
Ticker                  
HUDCO.NS        0.4190  
TITAGARH.NS     0.4664  
CHAMBLFERT.NS   0.5933  
KEC.NS          0.3796  
PGEL.NS         0.3128

I added some calculated columns regarded as mean/std. This metric can be used to compare the volatility of a statistics of many stocks (bigger is better). It can be seen from the summary table that **CHAMBLFERT.NS** and **KEC.NS**  are the stocks that have very high traded value throughout the considered period. This result is similar to the what has been observed visually from the previous visualizations.

The statistics of **Open** and **Volume** might provide insights into the source of the volatilities in the Traded Value of these stocks. By comparing the mean/std metrics of Open and Volume, we can see which source of volatility is stronger than the other. For example, for **KEC.NS**, the main source of volatility in Traded Value comes from the volatility in Volume as its mean/std metric is much lower than that of Open, which indicates that the changes in its Volume are more volatile. Using the same logic, the volatility sources of **CHAMBLFERT.NS** and **HUDCO** respectively come from their Volume, Price, and Volume

# MOVING AVERAGES

In [12]:
#Extracting the data for CHAMBLFERT.NS

df_smooth=final_df[final_df['Ticker']=='CHAMBLFERT.NS']

#Calculating the moving average of the stock in 30 50 100 and 250 days
#rolling is like window function which calculate the mean in the timeframes of about 30,50,100 and 250 days

df_smooth['MA30']=df_smooth['Open'].rolling(30).mean()
df_smooth['MA50']=df_smooth['Open'].rolling(30).mean()
df_smooth['MA100']=df_smooth['Open'].rolling(30).mean()
df_smooth['MA250']=df_smooth['Open'].rolling(30).mean()


#Creating the basic line chart to show MA 
fig_5=px.line(df_smooth,
            x='Date',
            y=['Open','MA30','MA50','MA100','MA250'],
            title='Moving Averages of CHAMBLFERT.NS',
            width=1000,
            height=600
            )

#Updating the layout of the chart
fig_5.update_layout(yaxis=default_yaxis,autosize=True,plot_bgcolor='white')

#adding slicer

fig_5.update_xaxes(rangeselector=default_RgSlct)

fig_5.show()

Different rolling windows offer different smoothing lines and seem to ignore information to different degrees. The MA100 price neglects lots of volatility in the price so the trend is strongly smoothed. The MA30 and MA50 lines are closer to the actualy trend in data as the smoothing effect is not as strong as that of MA100. The choice of the smoothing windows is really contextually dependent, so it is up to the analyst to decide.

# Volatility Analysis

This gives you the percentage change in price from one day to the next.

🔹 **Formula**:
                                     
$$
                                                  Rt=Pt−1/Pt−Pt−1

$$

In [13]:
#Filtering Columns
c_show=['Date','Close','Ticker']

#Extracting data from main DataFrame

df_closingP=final_df.loc[:,c_show]
df_closingP=final_df.pivot(index='Date',columns='Ticker',values='Close')

#Calculating the Daily percentage change

df_returns=df_closingP.pct_change()

df_returns.tail(30)


Ticker      CHAMBLFERT.NS  HUDCO.NS  KEC.NS  PGEL.NS  TITAGARH.NS
Date                                                             
2025-07-09         0.0014    0.0034  0.0213   0.0652      -0.0021
2025-07-10        -0.0076    0.0061 -0.0056  -0.0195       0.0085
2025-07-11        -0.0281   -0.0028 -0.0310  -0.0073      -0.0202
2025-07-14         0.0178    0.0031  0.0080   0.0208       0.0089
2025-07-15         0.0159    0.0083  0.0085   0.0322       0.0035
2025-07-16        -0.0023   -0.0033  0.0039   0.0236       0.0134
2025-07-17         0.0051   -0.0143 -0.0034  -0.0024      -0.0097
2025-07-18        -0.0113   -0.0135 -0.0049  -0.0206      -0.0205
2025-07-21         0.0056    0.0065  0.0012  -0.0026       0.0122
2025-07-22        -0.0027   -0.0094 -0.0091  -0.0224      -0.0129
2025-07-23         0.0158   -0.0011 -0.0119   0.0029      -0.0037
2025-07-24        -0.0080   -0.0007  0.0227   0.0128      -0.0184
2025-07-25        -0.0297   -0.0285 -0.0120  -0.0007      -0.0333
2025-07-28        -0.0151   -0.0194  0.0028  -0.0142      -0.0307
2025-07-29         0.0053    0.0092 -0.0041   0.0223       0.0257
2025-07-30         0.0103    0.0049  0.0148  -0.0019       0.0004
2025-07-31        -0.0433   -0.0237 -0.0131   0.0078      -0.0113
2025-08-01         0.0066   -0.0087 -0.0436  -0.0407      -0.0278
2025-08-04         0.0267    0.0403  0.0113   0.0137       0.0190
2025-08-05         0.0765   -0.0007  0.0104   0.0020       0.0066
2025-08-06         0.0035   -0.0316 -0.0172  -0.0492      -0.0179
2025-08-07        -0.0138   -0.0055 -0.0117  -0.0201       0.0138
2025-08-08        -0.0554   -0.0144 -0.0144  -0.2009      -0.0597
2025-08-11        -0.0156    0.0130 -0.0073  -0.1406      -0.0334
2025-08-12         0.0276    0.0016 -0.0037   0.0182       0.0300
2025-08-13        -0.0174   -0.0018 -0.0055  -0.0565       0.0176
2025-08-14         0.0025   -0.0007 -0.0179   0.0073      -0.0039
2025-08-18         0.0116    0.0093  0.0681   0.0795       0.0152
2025-08-19         0.0282    0.0156 -0.0042   0.0221       0.0072
2025-08-20         0.0238    0.0007 -0.0093  -0.0068       0.0062

In [14]:
df_returns.shape

(1484, 5)

The summary statistics of these stocks can be calculated easily by using the describe() method of the Pandas DataFrame. I also modify this table a bit so that it is more convenient to investigate the statistics

In [15]:
tab_sum2=df_returns.describe().T.sort_values(by='std', ascending=False)

tab_sum2

count   mean    std     min     25%     50%    75%    max
Ticker                                                                      
PGEL.NS       1,483.0000 0.0040 0.0371 -0.2009 -0.0182 -0.0007 0.0235 0.1968
TITAGARH.NS   1,483.0000 0.0027 0.0342 -0.1979 -0.0163  0.0000 0.0192 0.1992
HUDCO.NS      1,483.0000 0.0020 0.0302 -0.1999 -0.0131  0.0000 0.0140 0.1989
CHAMBLFERT.NS 1,483.0000 0.0014 0.0261 -0.1355 -0.0126  0.0011 0.0146 0.1929
KEC.NS        1,483.0000 0.0011 0.0249 -0.1874 -0.0122  0.0001 0.0127 0.1334

**mean** and std are the two important metrics that characterize each stock. When investigating a stock, **mean** daily percentage change is the return that an investor could expect to get from investing in it for a day, so it is regarded as expected return of the stock, **sd** is the standard deviation of the daily return and it shows the average deviation that the actual return deviate from the expected return. The larger **sd** is, the higher or lower the actual return might deviates from the expected return, so it is used to present the risk in the return of the stock. It should be noted that **mean** values in the table above is very small, but these are expected daily returns. When these returns compound over 365 days of the year, the equivalent annual returns would be much higher.

One way to compare these stocks by their characteristics is to use the Sharpe ratio. Without a given risk-free rate, the Sharpe ratio of each stock can be calculated by the following formula
                                                    
$$
                                                        \text{Sharpe Ratio} = \frac{R_p - R_f}{\sigma_p}
$$

Where:
- $R_p$ = Portfolio return
- $R_f$ = Risk-free rate
- $\sigma_p$ = Standard deviation of portfolio's excess return (volatility)                                                 

In [16]:
#finding the sharpe ratio using percent change mean
tab_sum2['S']=tab_sum2['mean']/tab_sum2['std']
tab_sum2.sort_values(by='S', ascending=False)

count   mean    std     min     25%     50%    75%    max  \
Ticker                                                                         
PGEL.NS       1,483.0000 0.0040 0.0371 -0.2009 -0.0182 -0.0007 0.0235 0.1968   
TITAGARH.NS   1,483.0000 0.0027 0.0342 -0.1979 -0.0163  0.0000 0.0192 0.1992   
HUDCO.NS      1,483.0000 0.0020 0.0302 -0.1999 -0.0131  0.0000 0.0140 0.1989   
CHAMBLFERT.NS 1,483.0000 0.0014 0.0261 -0.1355 -0.0126  0.0011 0.0146 0.1929   
KEC.NS        1,483.0000 0.0011 0.0249 -0.1874 -0.0122  0.0001 0.0127 0.1334   

                   S  
Ticker                
PGEL.NS       0.1066  
TITAGARH.NS   0.0793  
HUDCO.NS      0.0662  
CHAMBLFERT.NS 0.0539  
KEC.NS        0.0457

The Sharpe ratios show that **PGEL.NS** give the best return since 2019 and **KEC.NS** with least return among all 5

Next, let us confirm these insights by investigating the visualizations of stock returns. The changes in daily percentage returns overtime of these stocks are plotted below.

In [17]:
#creating the basic line chart for percentage change
fig_6=px.line(df_returns,
            x=df_returns.index,
            y=df_returns.columns,
            title='Changes in Daily Percentage',
            width=1000,
            height=600)

#Updating the layout of the chart to avoid clutter

fig_6.update_layout(yaxis=default_yaxis,autosize=True,plot_bgcolor='white')

#adding the slider
fig_6.update_xaxes(rangeselector=default_RgSlct)

fig_6.show()


We can see how these stocks volatile during the last 5 years. For a clearer insight, we can look at the box plots of the daily percentage changes.

In [18]:
fig_7=px.box(df_returns,
             title='Box plot for daily percentage change',
             width=1000,
             height=600
)

#updating the layout to avoid clutter
fig_7.update_layout(yaxis=default_yaxis,autosize=True, plot_bgcolor='white')

fig_7.show()

In [19]:
df_returns.corr()

Ticker         CHAMBLFERT.NS  HUDCO.NS  KEC.NS  PGEL.NS  TITAGARH.NS
Ticker                                                              
CHAMBLFERT.NS         1.0000    0.3271  0.2273   0.2714       0.2544
HUDCO.NS              0.3271    1.0000  0.2936   0.2504       0.3500
KEC.NS                0.2273    0.2936  1.0000   0.2118       0.2690
PGEL.NS               0.2714    0.2504  0.2118   1.0000       0.2303
TITAGARH.NS           0.2544    0.3500  0.2690   0.2303       1.0000

In [20]:
fig_8=px.imshow(df_returns.corr(),
                labels=dict(color='Correlation'),
                width=1000,
                height=600,
                text_auto='.3f'

)

#Adding the color scale

fig_8.update_xaxes(side='top')

fig_8.show()



It can be seen from the correlation matrix that the chosen stocks are all positively correlated to each other. However, the correlation varies depending on which pair of stocks is being considered. A scatter matrix plot is useful to have a more clear insight to these correlations.

In [21]:
#Simple Scatter matrix plot
fig_9=px.scatter_matrix(df_returns,
                        opacity=0.4,
                        width=800,
                        height=800,
)

#Updating the layout of the chart
fig_9.update_layout(yaxis=default_yaxis,autosize=True, plot_bgcolor='white')

fig_9.show()

# **Cumulative Return**
The cumulative return of a stock answer a more practical question. Suppose that I want to invest in a stock for a certain period and the stock does not pay dividend, then I would like to know how much I would get from the increase in the stock price afer the investment period I would like to have

In [22]:
df_cumR=(1+df_returns).cumprod()
df_cumR.tail(20)

Ticker      CHAMBLFERT.NS  HUDCO.NS  KEC.NS  PGEL.NS  TITAGARH.NS
Date                                                             
2025-07-23         4.7884   10.4260  3.5535 189.3321      26.0776
2025-07-24         4.7503   10.4186  3.6343 191.7491      25.5967
2025-07-25         4.6093   10.1214  3.5905 191.6175      24.7438
2025-07-28         4.5399    9.9246  3.6007 188.9013      23.9843
2025-07-29         4.5639   10.0158  3.5861 193.1132      24.5996
2025-07-30         4.6110   10.0653  3.6391 192.7423      24.6095
2025-07-31         4.4114    9.8265  3.5913 194.2380      24.3323
2025-08-01         4.4405    9.7413  3.4346 186.3407      23.6547
2025-08-04         4.5592   10.1334  3.4736 188.8893      24.1031
2025-08-05         4.9082   10.1260  3.5098 189.2722      24.2615
2025-08-06         4.9255    9.8056  3.4494 179.9510      23.8273
2025-08-07         4.8576    9.7519  3.4092 176.3374      24.1569
2025-08-08         4.5886    9.6117  3.3602 140.9072      22.7142
2025-08-11         4.5168    9.7367  3.3356 121.0921      21.9560
2025-08-12         4.6414    9.7524  3.3231 123.2938      22.6151
2025-08-13         4.5605    9.7348  3.3047 116.3298      23.0140
2025-08-14         4.5717    9.7283  3.2455 117.1794      22.9235
2025-08-18         4.6249    9.8186  3.4665 126.5006      23.2729
2025-08-19         4.7555    9.9717  3.4519 129.3005      23.4398
2025-08-20         4.8688    9.9792  3.4198 128.4151      23.5854

In [23]:
fig_10=px.line(df_cumR,
               x=df_cumR.index,
               y=df_cumR.columns,
               title='Cumulative Returns of Chosen Stocks',
               width=1000,
               height=600

               )

#Updating the layout of the chart
fig_10.update_layout(yaxis=default_yaxis,autosize=True, plot_bgcolor='white')

fig_10.update_xaxes(rangeselector=default_RgSlct)

fig_10.show()   

The cumulative returns plot shows the most and least profitable stocks over a 5-year period. **It can be seen clearly from the plot that PGEL could grow your 1 Rupee into 107 Rupees over the course of 6 year(return of approximately about **10,000%**)**

# **Conclusion
**In this project, I demonstrate my familiarity with Pandas and Plotly by constructing a stock analysis in Python using these packages. This stock analysis can be regarded as a technical analysis as it studies the patterns in the stocks' historical data.

                           PGEL.NS=Lowest Traded Value                HUDCO.NS=Highest Traded Value
                           KEC.NS=Lowest Sharpe Ratio                 PGEL.NS=Highest Sharpe 
                           KEC.NS=Lowest Cumulative Returns           PGEL.NS=Highest Cumulative return over 6 years
                                  over 6 years

This study can give you overview on how these stocks move for investing and Trading you have to deep dive into various **machine learning models**

**IMPROVEMENTS= would be implementing RANDOM FOREST REGRESSOR(A machine learning model) and on top of that i would try to train other models to get some learning experience**